In [1]:
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
pd.options.display.max_columns = None
pd.options.display.max_rows = None

In [3]:
# Cargar el archivo CSV
df = pd.read_csv('Driblab Scout -      Serie A 2024       La Liga 2024       France Ligue 1 2024       Championship 2024       Bundesliga 2 2024       Primaria FW - 31_01_2025 12_43.csv')
#CONVERTIR SI LAS COLUMNAS VIENEN DE TIPO 'OBJECT' Y QUEREMOS PASARLAS A NUMÉRICAS
cols_to_convert = df.loc[:, 'Partidos':'Secuencia acabada en tiro']
df[cols_to_convert.columns] = cols_to_convert.apply(pd.to_numeric, errors='coerce')
# Renombrar columnas
df = df.rename(columns= {
    'Temporada': 'Liga',
    'Altura (cm)': 'Altura',
    '% Duelos Aéreos': '% Duelos Aéreos Defensivos Ganados',
    'Asistencias Esperadas': 'xA',
    'Precisión en Centros': 'Precisión en Centros (Interceptar)',
    'Goles Esperados': 'xG',
    'Pases al Último ⅓': 'Pases al Último ⅓ Completados',
    '% Duelos Defensivos': '% Duelos Defensivos Ganados',
    'Acciones Agresivas': 'Presión tras pérdida',
    '% Progresión de Balón en Campo Rival en su Equipo': '% Progr Balón Campo Rival en su Equipo'
})

# Crear nuevas columnas
df['Recuperaciones en Campo Propio'] = df['Recuperaciones'] - df['Recuperaciones en Campo Contrario']
df['Faltas en Campo Propio'] = ((df['Faltas'] * df['% Faltas en Campo Propio']) / 100)
df['Faltas en Campo Rival'] = (df['Faltas'] - df['Faltas en Campo Propio'])
df['Centros en Jugada'] = ((df['Centros Completados en Jugada'] * 100) / df['% Centros Completados en Jugada'])
df['Pases al Área en Juego'] = ((df['Pases Completados al Área en Juego'] * 100) / df['% Pases al Área en Jugada'])
df['Pases Adelante'] = ((df['Pases'] * df['% Pases hacia delante']) / 100)
df['Pases Adelante Completados'] = ((df['Pases Adelante'] * df['% Pases Adelante Completados']) / 100)
df['Duelos Defensivos Ganados'] = ((df['Duelos Defensivos'] * df['% Duelos Defensivos Ganados']) / 100)
df['Pases al Último ⅓'] = ((df['Pases al Último ⅓ Completados'] * 100) / df['% Pases al Último ⅓'])
df['Pases Progresivos'] = ((df['Pases Progresivos Completados'] * 100) / df['% Pases Progresivos'])
df['Pases Largos'] = ((df['Pases Largos Completados'] * 100) / df['% Pases Largos'])
df['% Pases Largos del total'] = ((df['Pases Largos'] * 100) / df['Pases'])
df['Pases Clave (Total)'] = ((df['Pases Clave en Juego'] * df['Minutos']) / 90).round(0)
df['Ocasiones Creadas (Total)'] = ((df['Ocasiones Creadas en Jugada'] * df['Minutos']) / 90).round(0)
df['Duelos Aéreos Área Propia'] = ((df['Duelos Aéreos Ganados en AP'] * 100) / df['% Duelos Aéreos Ganados Área Propia'])
df['Duelos Aéreos Área Rival'] = ((df['Duelos Aéreos Ganados en AR'] * 100) / df['% Duelos Aéreos Ganados Área Rival'])
df['Pérdidas en Campo Rival'] = df['Pérdidas'] - df['Pérdidas en Campo Propio']

# Redondear a 2 decimales y llenar valores nulos con 0
df = df.round(2)
df.fillna(0, inplace=True)

# Ver las primeras 5 filas
print(df.sample(5))


             Nombre            Equipo Posición         Liga  Valor (€)  \
42    Kieffer Moore  Sheffield United       FW  ENG II 2024     1200.0   
107  Gorka Guruzeta     Athletic Club       FW   ESP I 2024    15000.0   
234   Manuel Fuster     UD Las Palmas       FW   ESP I 2024     1500.0   
276     David Costa              Lens       FW   FRA I 2024     7000.0   
82     Zan Vipotnik           Swansea       FW  ENG II 2024     2500.0   

    Fin de contrato  Edad  Altura          Lado Pie bueno  GBE  Partidos  \
42           Jun 27    32   196.0   Left/Centre     right   18        20   
107          Jun 28    28   188.0        Centre     right   27        20   
234          Jun 28    27   169.0    Left/Right     right   17        15   
276          Jun 26    24   168.0  Centre/Right     right   22        11   
82           Jul 28    22   185.0        Centre      both   15        26   

     Minutos  Tarjetas Amarillas  Tarjetas Rojas  Distancia Media de Pases  \
42      1597        

In [4]:
# media de minutos para cada Liga
mean_minutos_por_temporada = df.groupby('Liga')['Minutos'].mean()

mean_minutos_por_temporada

Liga
ENG II 2024    832.078431
ESP I 2024     759.740741
FRA I 2024     627.311688
GER II 2024    718.872093
ITA I 2024     781.707865
Name: Minutos, dtype: float64

In [5]:
# Calcular la media de minutos para cada liga
mean_minutos_por_temporada = df.groupby('Liga')['Minutos'].mean()

#Filtro sólo a los delanteros.
df_delantero = df[df.apply(
    lambda row: row['Minutos'] >= mean_minutos_por_temporada[row['Liga']] and row['Posición'] in ['FW'], axis=1
)]

# Mostrar el DataFrame filtrado
print(df_delantero)


                            Nombre                  Equipo Posición  \
0                    Wilson Isidor              Sunderland       FW   
1                      Jerry Yates            Derby County       FW   
2                   Elijah Adebayo              Luton Town       FW   
3                        Josh Maja               West Brom       FW   
4                   Carlton Morris              Luton Town       FW   
5                      Vakoun Bayo                 Watford       FW   
6                        Emil Riis       Preston North End       FW   
7                    Rubin Colwill                 Cardiff       FW   
8                    Thomas Cannon              Stoke City       FW   
9                      Mark Harris           Oxford United       FW   
10                      Ante Crnac            Norwich City       FW   
11             Emmanuel Latte Lath           Middlesbrough       FW   
12                 Roberto Piccoli                Cagliari       FW   
13    

In [6]:
# Función para calcular la media y el percentil 75 por liga
def agregar_media_y_p75_por_liga(df):
    # Crear un DataFrame vacío para almacenar resultados
    lista_resultados = []
    
    # Iteramos sobre cada liga
    for liga, grupo in df.groupby('Liga'):
        # Calcular la media de las métricas numéricas
        media = grupo.select_dtypes(include=['number']).mean()
        media_df = pd.DataFrame(media).transpose()
        media_df['Nombre'] = f'MEDIAdc_{liga}'  # Identificar la liga en el nombre
        media_df['Liga'] = liga  # Asegurar que se mantenga la liga
        
        # Calcular el percentil 75 de las métricas numéricas
        percen = grupo.select_dtypes(include=['number']).quantile(0.75)
        percen_df = pd.DataFrame(percen).transpose()
        percen_df['Nombre'] = f'p75dc_{liga}'  # Identificar la liga en el nombre
        percen_df['Liga'] = liga  # Asegurar que se mantenga la liga
        
        # Concatenar media y percentil para esta liga
        lista_resultados.append(media_df)
        lista_resultados.append(percen_df)
    
    # Concatenar todos los DataFrames obtenidos por liga
    return pd.concat(lista_resultados, ignore_index=True)

# Llamar a la función para calcular media y percentil 75 por liga
media_y_p75 = agregar_media_y_p75_por_liga(df_delantero)

# Concatenar el DataFrame original con las nuevas filas (media y percentil 75 por liga)
df_delantero = pd.concat([df_delantero, media_y_p75], ignore_index=True)

# Calcular el percentil 25 por liga para 'Pérdidas'
p25_perdidas = df_delantero.groupby('Liga')['Pérdidas'].quantile(0.25)

# Asignar los valores al DataFrame para las filas que empiezan con 'p75dc'
for liga in p25_perdidas.index:  # Iterar sobre las ligas
    df_delantero.loc[
        (df_delantero['Nombre'].str.startswith('p75dc')) & (df_delantero['Liga'] == liga),
        'Pérdidas'
    ] = p25_perdidas[liga]

# Calcular el percentil 25 por liga para 'Pérdidas en Campo Propio'
p25_perdidas_campo = df_delantero.groupby('Liga')['Pérdidas en Campo Propio'].quantile(0.25)

# Asignar los valores al DataFrame para las filas que empiezan con 'p75dc'
for liga in p25_perdidas_campo.index:  # Iterar sobre las ligas
    df_delantero.loc[
        (df_delantero['Nombre'].str.startswith('p75dc')) & (df_delantero['Liga'] == liga),
        'Pérdidas en Campo Propio'
    ] = p25_perdidas_campo[liga]

# Asegurarse de que 'Posición' no tenga valores nulos
df_delantero['Posición'] = df_delantero['Posición'].fillna('Delantero')

# Separar las columnas numéricas y no numéricas
columnas_no_numericas = df_delantero.select_dtypes(exclude=[int, float])
columnas_no_numericas['Edad'] = df_delantero['Edad']

columnas_numericas = df_delantero.select_dtypes(include=[int, float]).round(2)
columnas_numericas = columnas_numericas.drop('Edad', axis=1)

# Unir las columnas no numéricas con los datos numéricos
delanterocentro = columnas_no_numericas.join(columnas_numericas)

# Mostrar las últimas filas del DataFrame
print(delanterocentro.tail(5))


                  Nombre Equipo   Posición         Liga Fin de contrato Lado  \
208     p75dc_FRA I 2024    NaN  Delantero   FRA I 2024             NaN  NaN   
209  MEDIAdc_GER II 2024    NaN  Delantero  GER II 2024             NaN  NaN   
210    p75dc_GER II 2024    NaN  Delantero  GER II 2024             NaN  NaN   
211   MEDIAdc_ITA I 2024    NaN  Delantero   ITA I 2024             NaN  NaN   
212     p75dc_ITA I 2024    NaN  Delantero   ITA I 2024             NaN  NaN   

    Pie bueno       Edad  Valor (€)  Altura    GBE  Partidos  Minutos  \
208       NaN  29.000000   13500.00  185.00  23.50     18.00  1190.50   
209       NaN  25.977273    1823.86  185.57   9.75     16.89  1144.27   
210       NaN  28.500000    2625.00  187.25  11.00     19.00  1373.00   
211       NaN  25.916667   19680.56  184.22  26.17     19.42  1423.08   
212       NaN  27.250000   25000.00  189.00  29.00     21.00  1652.25   

     Tarjetas Amarillas  Tarjetas Rojas  Distancia Media de Pases  \
208        

In [7]:
# Importaciones
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from datetime import datetime  # Importamos datetime para manejar fechas

# Configuración inicial
scaler = MinMaxScaler()

# Definición de métricas y pesos
METRICS_CONFIG = {
    'metrics': [
        'Remates', 'Tiros a puerta', '% Remates a Puerta', 'xG', 'xG por Remate',
        'Eficiencia xG', 'xA en Jugada', 'Regates Intentados Último ⅓',
        'Regates Completados Último ⅓', '% Regates Completados Último ⅓',
        'Faltas Recibidas', 'Pases Progresivos Recibidos en el Área',
        'Toques en Área Rival', 'Pérdidas', 'Pérdidas en Campo Propio',
        'Pases', 'Pases Completados', '% Pases', '% Pases Último ⅓',
        'Pases Clave en Juego', 'Duelos Aéreos Totales Campo Rival',
        '% Duelos Aéreos Ganados Campo Rival', 'Duelos', '% Duelos Exitosos'
    ],
    'weights': {
        'Remates': 1.1,
        'Tiros a puerta': 0.7,
        '% Remates a Puerta': 0.7,
        'xG': 0.7,
        'xG por Remate': 1.1,
        'Eficiencia xG': 0.7,
        'xA en Jugada': 0.2,
        'Regates Intentados Último ⅓': 0.2,
        'Regates Completados Último ⅓': 0.1,
        '% Regates Completados Último ⅓': 0.2,
        'Faltas Recibidas': 0.2,
        'Pases Progresivos Recibidos en el Área': 0.4,
        'Toques en Área Rival': 0.2,
        'Pérdidas': 0.5,
        'Pérdidas en Campo Propio': 0.2,
        'Pases': 0.2,
        'Pases Completados': 0.2,
        '% Pases': 0.4,
        '% Pases Último ⅓': 0.2,
        'Pases Clave en Juego': 0.2,
        'Duelos Aéreos Totales Campo Rival': 0.2,
        '% Duelos Aéreos Ganados Campo Rival': 0.4,
        'Duelos': 0.4,
        '% Duelos Exitosos': 0.6
    },
    'invert_metrics': ['Pérdidas', 'Pérdidas en Campo Propio']  # Métricas donde 0 es mejor
}

YEAR_MAPPING = {
    '24': 2024, '25': 2025, '26': 2026, '27': 2027,
    '28': 2028, '29': 2029, '30': 2030, '31': 2031
}

# Función para calcular el rating
def calcular_rating(df):
    """Calcula el rating de jugadores normalizando métricas y aplicando pesos."""
    # Normalización por liga
    df[METRICS_CONFIG['metrics']] = scaler.fit_transform(df[METRICS_CONFIG['metrics']])
    
    # Cálculo automático del rating usando comprensión de diccionario
    rating_components = []
    for metric, weight in METRICS_CONFIG['weights'].items():
        if metric in METRICS_CONFIG['invert_metrics']:
            rating_components.append((1 - df[metric]) * weight)
        else:
            rating_components.append(df[metric] * weight)
    
    df['Rating'] = sum(rating_components)
    
    # Ordenamiento y ranking
    df = df.sort_values('Rating', ascending=False)
    df['rank'] = df['Rating'].rank(ascending=False, method='min')
    
    return df

# Función para procesar contratos
def procesar_contratos(df):
    """Procesa la información de contratos y formato numérico."""
    # Filtrar contratos para ligas 2024
    mask_2024 = df['Liga'].str.contains('2024', na=False)
    df['Fin de contrato'] = df['Fin de contrato'].where(mask_2024)
    
    # Extraer y mapear años
    df['Año fin contrato'] = (
        df['Fin de contrato']
        .str.extract(r'(\d{2})$')[0]
        .map(YEAR_MAPPING)
    )
    
    # Formato numérico para Europa
    numeric_cols = df.select_dtypes(include=['number']).columns
    df[numeric_cols] = df[numeric_cols].applymap(lambda x: f"{x:,}".replace(',', ' ').replace('.', ','))
    
    return df

# Carga de datos (simulado)
# delanterocentro = pd.read_csv('tus_datos.csv')

# Añadir columna con la fecha de ejecución
fecha_ejecucion = datetime.now().strftime('%Y-%m-%d')  # Formato: Año-Mes-Día
delanterocentro['Fecha Ejecución'] = fecha_ejecucion

# Procesamiento principal
delanterocentro = (
    delanterocentro
    .groupby('Liga', group_keys=False)
    .apply(calcular_rating)
    .pipe(procesar_contratos)
)

# Guardar resultados con fecha en el nombre del archivo
output_file_path = f'delantero_centro_ratings_{fecha_ejecucion}.csv'  # Nombre con fecha
delanterocentro.to_csv(output_file_path, index=False)

print(f"Archivo guardado en: {output_file_path}")

Archivo guardado en: delantero_centro_ratings_2025-01-31.csv


C:\Users\RafaelMorenodelRio\AppData\Local\Temp\ipykernel_384\2132041917.py:108: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(calcular_rating)
C:\Users\RafaelMorenodelRio\AppData\Local\Temp\ipykernel_384\2132041917.py:93: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df[numeric_cols] = df[numeric_cols].applymap(lambda x: f"{x:,}".replace(',', ' ').replace('.', ','))


In [8]:
delanterocentro

Nombre                  Equipo   Posición  \
123                   Tommy Conway           Middlesbrough         FW   
53                 Callum Robinson                 Cardiff         FW   
11             Emmanuel Latte Lath           Middlesbrough         FW   
204              p75dc_ENG II 2024                     NaN  Delantero   
2                   Elijah Adebayo              Luton Town         FW   
153                Milutin Osmajic       Preston North End         FW   
83                     Nahki Wells            Bristol City         FW   
151             Sinclair Armstrong            Bristol City         FW   
18                      Joel Piroe                   Leeds         FW   
81                    Mateo Joseph                   Leeds         FW   
4                   Carlton Morris              Luton Town         FW   
5                      Vakoun Bayo                 Watford         FW   
88                    Josh Sargent            Norwich City         FW   
8                    Thomas Cannon              Stoke City         FW   
101                  Michael Smith     Sheffield Wednesday         FW   
48                 Eliezer Mayenda              Sunderland         FW   
129               Mihailo Ivanovic                Millwall         FW   
3                        Josh Maja               West Brom         FW   
117                   Michael Frey     Queens Park Rangers         FW   
144                    Jacob Brown              Luton Town         FW   
0                    Wilson Isidor              Sunderland         FW   
6                        Emil Riis       Preston North End         FW   
80           Brandon Thomas Asante           Coventry City         FW   
63                     Ellis Simms           Coventry City         FW   
69                   Zian Flemming                 Burnley         FW   
154                Norman Bassette           Coventry City         FW   
42                   Kieffer Moore        Sheffield United         FW   
203            MEDIAdc_ENG II 2024                     NaN  Delantero   
7                    Rubin Colwill                 Cardiff         FW   
135              Florian Bianchini                 Swansea         FW   
82                    Zan Vipotnik                 Swansea         FW   
47                      Joao Pedro               Hull City         FW   
68                   Makhtar Gueye        Blackburn Rovers         FW   
10                      Ante Crnac            Norwich City         FW   
93                    Colby Bishop              Portsmouth         FW   
1                      Jerry Yates            Derby County         FW   
51                     Yuki Ohashi        Blackburn Rovers         FW   
15                   Sam Greenwood       Preston North End         FW   
155                     Jamal Lowe     Sheffield Wednesday         FW   
134                    Chris Bedia               Hull City         FW   
127                      Zan Celar     Queens Park Rangers         FW   
138                 Rhian Brewster        Sheffield United         FW   
9                      Mark Harris           Oxford United         FW   
142                    Lyle Foster                 Burnley         FW   
159                  Dane Scarlett           Oxford United         FW   
73                     Ryan Hardie         Plymouth Argyle         FW   
156                Michael Obafemi         Plymouth Argyle         FW   
60              Macaulay Langstaff                Millwall         FW   
132               Christian Saydee              Portsmouth         FW   
174                  Jay Rodriguez                 Burnley         FW   
96                        Ike Ugbo     Sheffield Wednesday         FW   
23                   Kylian Mbappe             Real Madrid         FW   
162              Alexander Sorloth         Atletico Madrid         FW   
29              Robert Lewandowski            FC Barcelona         FW   
95           